https://www.kaggle.com/datasets/andrexibiza/grocery-sales-dataset/data

In [0]:
display(dbutils.fs.ls("/FileStore/tables/DadosVendas"))

path name size modificationTime dbfs:/FileStore/tables/DadosVendas/Untitled___Frame_1.jpg Untitled___Frame_1.jpg 64587 1744379343000 dbfs:/FileStore/tables/DadosVendas/categories.csv categories.csv 137 1742582641000 dbfs:/FileStore/tables/DadosVendas/cities.csv cities.csv 2170 1742582641000 dbfs:/FileStore/tables/DadosVendas/countries.csv countries.csv 3179 1742582629000 dbfs:/FileStore/tables/DadosVendas/customers.csv customers.csv 4436738 1742582640000 dbfs:/FileStore/tables/DadosVendas/employees.csv employees.csv 1715 1742582630000 dbfs:/FileStore/tables/DadosVendas/products.csv products.csv 36846 1742582631000 dbfs:/FileStore/tables/DadosVendas/sales.csv sales.csv 517020842 1742582689000

## 🎯 Objetivo do Projeto

O objetivo deste projeto é construir uma arquitetura de dados em camadas (Bronze, Silver e Gold) para processar, modelar e analisar um conjunto de dados de vendas, visando responder perguntas de negócio relacionadas ao desempenho de vendas, comportamento dos clientes e performance de produtos. O problema a ser resolvido está relacionado à falta de visibilidade centralizada e confiável para tomada de decisão estratégica com base nas transações de vendas.


## 📥 Coleta de Dados

Os dados foram coletados a partir de arquivos CSV disponíveis no diretório `/FileStore/tables/DadosVendas/`, contendo informações brutas sobre produtos, clientes, vendas, localidades e funcionários. Estes arquivos foram carregados na camada Bronze da arquitetura usando a linguagem SQL no Databricks.

A seguir, a lista de arquivos utilizados:
- categories.csv
- cities.csv
- countries.csv
- customers.csv
- employees.csv
- products.csv
- sales.csv

## 🔄 Carga dos Dados

Os dados foram carregados das tabelas Bronze para Silver aplicando transformação, limpeza e enriquecimento, como junções entre entidades, normalização de colunas e tipagem correta.

Em seguida, os dados da camada Silver foram agregados e refinados para alimentar as tabelas Gold, focadas em análise de negócio.

As cargas foram feitas utilizando PySpark e SQL, com persistência em formato Delta e uso de `saveAsTable` para garantir armazenamento eficiente na nuvem via Databricks.


## 📊 Perguntas a serem respondidas na análise

- Quais são os clientes mais ativos mensalmente, considerando número de compras, itens adquiridos e valor total gasto? *(gold.compras_clientes_resumo_mensal)*

- Como evoluíram as vendas ao longo dos meses e anos? Qual o valor total vendido, ticket médio e número de vendas por período? ✅ *(gold.vendas_resumo_mensal)*

- Quais os países e cidades com maior volume de vendas? *(gold.vendas_local)*

- Quais cidades concentram o maior número de clientes registrados? *(derivado de gold.compras_clientes_resumo_mensal ou silver.dim_clientes)*

- Em quais cidades os clientes possuem maior frequência ou volume de compras? *(gold.compras_clientes_resumo_mensal + análise cruzada com silver.dim_cidades)*

- Qual a categoria de produto mais vendida em cada país ou cidade? *(usar gold.fato_vendas ou criar gold.categoria_venda_local)*

- Qual a classe de produto com maior volume de vendas por localidade (cidade/país)? *(requer criação de uma gold.classe_produto_local com base em gold.fato_vendas)*

- Quais produtos geram mais receita? *(gold.top_produtos)*

- Qual o ticket médio por produto e como ele varia entre categorias? *(gold.ticket_medio_produto)*

- Qual foi a data da última venda de cada produto e qual o tempo desde a última venda? *(gold.ultima_venda_produto)*

- Qual a recência dos clientes (dias desde a última compra)? *(gold.recencia_clientes)*


# 🥉 Camada Bronze – Dados Brutos

> Responsável por armazenar os dados na sua forma original, sem transformações, apenas com padronizações mínimas (ex: tipos e nomes de colunas).

### Tabelas Bronze:
- `bronze.raw_categorias`
- `bronze.raw_cidades`
- `bronze.raw_paises`
- `bronze.raw_clientes`
- `bronze.raw_funcionarios`
- `bronze.raw_produtos`
- `bronze.raw_vendas`

---

## 🔶 Script SQL: Criação e Carga Inicial da Camada Bronze

In [0]:
%sql

DROP DATABASE IF EXISTS bronze CASCADE;
CREATE DATABASE IF NOT EXISTS bronze;

DROP TABLE IF EXISTS bronze.raw_categorias PURGE;
DROP TABLE IF EXISTS bronze.raw_cidades PURGE;
DROP TABLE IF EXISTS bronze.raw_paises PURGE;
DROP TABLE IF EXISTS bronze.raw_clientes PURGE;
DROP TABLE IF EXISTS bronze.raw_funcionarios PURGE;
DROP TABLE IF EXISTS bronze.raw_produtos PURGE;
DROP TABLE IF EXISTS bronze.raw_vendas PURGE;

USE bronze;
CREATE TABLE IF NOT EXISTS raw_categorias
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/categories.csv',
  'inferSchema' 'true',
  'header' 'true'
);

CREATE TABLE IF NOT EXISTS raw_cidades
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/cities.csv',
  'inferSchema' 'true',
  'header' 'true'
);

CREATE TABLE IF NOT EXISTS raw_paises
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/countries.csv',
  'inferSchema' 'true',
  'header' 'true'
);

CREATE TABLE IF NOT EXISTS raw_clientes
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/customers.csv',
  'inferSchema' 'true',
  'header' 'true'
);

CREATE TABLE IF NOT EXISTS raw_funcionarios
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/employees.csv',
  'inferSchema' 'true',
  'header' 'true'
);

CREATE TABLE IF NOT EXISTS raw_produtos
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/products.csv',
  'inferSchema' 'true',
  'header' 'true'
);

CREATE TABLE IF NOT EXISTS raw_vendas
USING CSV
OPTIONS (
  'path' '/FileStore/tables/DadosVendas/sales.csv',
  'inferSchema' 'true',
  'header' 'true'
);

In [0]:
display(spark.sql("SELECT * FROM bronze.raw_categorias LIMIT 10"))
display(spark.sql("SELECT * FROM bronze.raw_cidades LIMIT 10"))
display(spark.sql("SELECT * FROM bronze.raw_paises LIMIT 10"))
display(spark.sql("SELECT * FROM bronze.raw_clientes LIMIT 10"))
display(spark.sql("SELECT * FROM bronze.raw_funcionarios LIMIT 10"))
display(spark.sql("SELECT * FROM bronze.raw_produtos LIMIT 10"))
display(spark.sql("SELECT * FROM bronze.raw_vendas LIMIT 10"))

CategoryID CategoryName 1 Confections 2 Shell fish 3 Cereals 4 Dairy 5 Beverages 6 Seafood 7 Meat 8 Grain 9 Poultry 10 Snails

CityID CityName Zipcode CountryID 1 Dayton 80563 32 2 Buffalo 17420 32 3 Chicago 44751 32 4 Fremont 20641 32 5 Virginia Beach 62389 32 6 Austin 781 32 7 Riverside 1439 32 8 Arlington 12654 32 9 Atlanta 66212 32 10 Toledo 52048 32

CountryID CountryName CountryCode 1 Armenia AN 2 Canada FO 3 Belize MK 4 Uganda LV 5 Thailand VI 6 Tunisia GF 7 Montserrat MM 8 Iraq AO 9 Slovakia CG 10 Germany TT

CustomerID FirstName MiddleInitial LastName CityID Address 1 Stefanie Y Frye 79 97 Oak Avenue 2 Sandy T Kirby 96 52 White First Freeway 3 Lee T Zhang 55 921 White Fabien Avenue 4 Regina S Avery 40 75 Old Avenue 5 Daniel S Mccann 2 283 South Green Hague Avenue 6 Dennis H Zuniga 6 20 West Old Road 7 Myra K Jefferson 68 26 Green First Parkway 8 Teddy L Parsons 44 38 West Nobel St. 9 Annie F Stein 46 17 White Nobel Way 10 Herman Y Pope 72 695 Old Street

EmployeeID FirstName MiddleInitial LastName BirthDate Gender CityID HireDate 1 Nicole T Fuller 1981-03-07T00:00:00Z F 80 2011-06-20T07:15:36.92Z 2 Christine W Palmer 1968-01-25T00:00:00Z F 4 2011-04-27T04:07:56.93Z 3 Pablo Y Cline 1963-02-09T00:00:00Z M 70 2012-03-30T18:55:23.27Z 4 Darnell O Nielsen 1989-02-06T00:00:00Z M 39 2014-03-06T06:55:02.78Z 5 Desiree L Stuart 1963-05-03T00:00:00Z F 23 2014-11-16T22:59:54.72Z 6 Holly E Collins 1987-01-13T00:00:00Z M 65 2013-06-22T13:20:18.08Z 7 Chadwick P Cook 1970-05-02T00:00:00Z M 39 2016-07-10T06:22:00.67Z 8 Julie E Dyer 1956-12-13T00:00:00Z M 18 2014-10-14T23:12:53.42Z 9 Daphne X King 1956-05-02T00:00:00Z F 39 2013-04-17T14:48:02.7Z 10 Jean P Vang 1963-12-30T00:00:00Z M 9 2012-07-23T15:02:12.64Z

ProductID ProductName Price CategoryID Class ModifyDate Resistant IsAllergic VitalityDays 1 Flour - Whole Wheat 74.2988 3 Medium 2018-02-16T08:21:49.19Z Durable Unknown 0.0 2 Cookie Chocolate Chip With 91.2329 3 Medium 2017-02-12T11:39:10.97Z Unknown Unknown 0.0 3 Onions - Cippolini 9.1379 9 Medium 2018-03-15T08:11:51.56Z Weak False 111.0 4 Sauce - Gravy, Au Jus, Mix 54.3055 9 Medium 2017-07-16T00:46:28.88Z Durable Unknown 0.0 5 Artichokes - Jerusalem 65.4771 2 Low 2017-08-16T14:13:35.43Z Durable True 27.0 6 Wine - Magnotta - Cab Sauv 79.7184 8 High 2017-05-25T15:08:39.69Z Unknown Unknown 0.0 7 Table Cloth - 53x69 Colour 31.837 9 Medium 2017-02-24T15:14:30.05Z Durable False 0.0 8 Halibut - Steaks 89.8573 5 Medium 2018-03-24T05:21:21.89Z Unknown True 108.0 9 Rabbit - Whole 84.4219 11 Medium 2017-06-17T12:12:04.67Z Durable Unknown 0.0 10 Scampi Tail 95.0957 4 Low 2017-07-30T10:11:45.99Z Weak True 105.0

SalesID SalesPersonID CustomerID ProductID Quantity Discount TotalPrice SalesDate TransactionNumber 1 6 27039 381 7 0.0 0.0 2018-02-05T07:38:25.43Z FQL4S94E4ME1EZFTG42G 2 16 25011 61 7 0.0 0.0 2018-02-02T16:03:31.15Z 12UGLX40DJ1A5DTFBHB8 3 13 94024 23 24 0.0 0.0 2018-05-03T19:31:56.88Z 5DT8RCPL87KI5EORO7B0 4 8 73966 176 19 0.2 0.0 2018-04-07T14:43:55.42Z R3DR9MLD5NR76VO17ULE 5 10 32653 310 9 0.0 0.0 2018-02-12T15:37:03.94Z 4BGS0Z5OMAZ8NDAFHHP3 6 13 28663 413 8 0.0 0.0 2018-02-07T10:33:24.99Z 3KTAYIZPGDQMZMRWZ8NG 7 14 46674 370 12 0.0 0.0 2018-03-02T23:09:58.75Z ICRZIHELQCVB71RNH1G5 8 3 12687 287 4 0.2 0.0 2018-01-17T13:41:38.46Z 6X9MOQIJH92NIK81BG0K 9 16 89009 124 23 0.0 0.0 2018-04-27T06:19:58.57Z P0UARL09H66APBEIDUQW 10 22 65017 346 17 0.2 0.0 2018-03-26T22:12:08.53Z 92TNPGIL6LFKVGWFBW5H

In [0]:
bronze_tables = {
    "raw_categorias": "Categorias de produtos",
    "raw_cidades": "Cidades dos clientes e funcionários",
    "raw_paises": "Países relacionados às cidades",
    "raw_clientes": "Clientes da base de vendas",
    "raw_funcionarios": "Funcionários/vendedores",
    "raw_produtos": "Produtos vendidos",
    "raw_vendas": "Fato de vendas realizadas"
}

for table, descricao in bronze_tables.items():
    print(f"\n📦 Tabela Bronze: {table} — {descricao}")
    display(spark.sql(f"SELECT * FROM bronze.{table} LIMIT 10"))



📦 Tabela Bronze: raw_categorias — Categorias de produtos


CategoryID CategoryName 1 Confections 2 Shell fish 3 Cereals 4 Dairy 5 Beverages 6 Seafood 7 Meat 8 Grain 9 Poultry 10 Snails


📦 Tabela Bronze: raw_cidades — Cidades dos clientes e funcionários


CityID CityName Zipcode CountryID 1 Dayton 80563 32 2 Buffalo 17420 32 3 Chicago 44751 32 4 Fremont 20641 32 5 Virginia Beach 62389 32 6 Austin 781 32 7 Riverside 1439 32 8 Arlington 12654 32 9 Atlanta 66212 32 10 Toledo 52048 32


📦 Tabela Bronze: raw_paises — Países relacionados às cidades


...

EmployeeID FirstName MiddleInitial LastName BirthDate Gender CityID HireDate 1 Nicole T Fuller 1981-03-07T00:00:00Z F 80 2011-06-20T07:15:36.92Z 2 Christine W Palmer 1968-01-25T00:00:00Z F 4 2011-04-27T04:07:56.93Z 3 Pablo Y Cline 1963-02-09T00:00:00Z M 70 2012-03-30T18:55:23.27Z 4 Darnell O Nielsen 1989-02-06T00:00:00Z M 39 2014-03-06T06:55:02.78Z 5 Desiree L Stuart 1963-05-03T00:00:00Z F 23 2014-11-16T22:59:54.72Z 6 Holly E Collins 1987-01-13T00:00:00Z M 65 2013-06-22T13:20:18.08Z 7 Chadwick P Cook 1970-05-02T00:00:00Z M 39 2016-07-10T06:22:00.67Z 8 Julie E Dyer 1956-12-13T00:00:00Z M 18 2014-10-14T23:12:53.42Z 9 Daphne X King 1956-05-02T00:00:00Z F 39 2013-04-17T14:48:02.7Z 10 Jean P Vang 1963-12-30T00:00:00Z M 9 2012-07-23T15:02:12.64Z


📦 Tabela Bronze: raw_produtos — Produtos vendidos


ProductID ProductName Price CategoryID Class ModifyDate Resistant IsAllergic VitalityDays 1 Flour - Whole Wheat 74.2988 3 Medium 2018-02-16T08:21:49.19Z Durable Unknown 0.0 2 Cookie Chocolate Chip With 91.2329 3 Medium 2017-02-12T11:39:10.97Z Unknown Unknown 0.0 3 Onions - Cippolini 9.1379 9 Medium 2018-03-15T08:11:51.56Z Weak False 111.0 4 Sauce - Gravy, Au Jus, Mix 54.3055 9 Medium 2017-07-16T00:46:28.88Z Durable Unknown 0.0 5 Artichokes - Jerusalem 65.4771 2 Low 2017-08-16T14:13:35.43Z Durable True 27.0 6 Wine - Magnotta - Cab Sauv 79.7184 8 High 2017-05-25T15:08:39.69Z Unknown Unknown 0.0 7 Table Cloth - 53x69 Colour 31.837 9 Medium 2017-02-24T15:14:30.05Z Durable False 0.0 8 Halibut - Steaks 89.8573 5 Medium 2018-03-24T05:21:21.89Z Unknown True 108.0 9 Rabbit - Whole 84.4219 11 Medium 2017-06-17T12:12:04.67Z Durable Unknown 0.0 10 Scampi Tail 95.0957 4 Low 2017-07-30T10:11:45.99Z Weak True 105.0


📦 Tabela Bronze: raw_vendas — Fato de vendas realizadas


SalesID SalesPersonID CustomerID ProductID Quantity Discount TotalPrice SalesDate TransactionNumber 1 6 27039 381 7 0.0 0.0 2018-02-05T07:38:25.43Z FQL4S94E4ME1EZFTG42G 2 16 25011 61 7 0.0 0.0 2018-02-02T16:03:31.15Z 12UGLX40DJ1A5DTFBHB8 3 13 94024 23 24 0.0 0.0 2018-05-03T19:31:56.88Z 5DT8RCPL87KI5EORO7B0 4 8 73966 176 19 0.2 0.0 2018-04-07T14:43:55.42Z R3DR9MLD5NR76VO17ULE 5 10 32653 310 9 0.0 0.0 2018-02-12T15:37:03.94Z 4BGS0Z5OMAZ8NDAFHHP3 6 13 28663 413 8 0.0 0.0 2018-02-07T10:33:24.99Z 3KTAYIZPGDQMZMRWZ8NG 7 14 46674 370 12 0.0 0.0 2018-03-02T23:09:58.75Z ICRZIHELQCVB71RNH1G5 8 3 12687 287 4 0.2 0.0 2018-01-17T13:41:38.46Z 6X9MOQIJH92NIK81BG0K 9 16 89009 124 23 0.0 0.0 2018-04-27T06:19:58.57Z P0UARL09H66APBEIDUQW 10 22 65017 346 17 0.2 0.0 2018-03-26T22:12:08.53Z 92TNPGIL6LFKVGWFBW5H

#🥈 Camada Silver – Dados Tratados

> Nessa camada os dados são limpos, normalizados e enriquecidos. É onde ocorre a modelagem dimensional com tabelas de dimensões e fatos.

### Tabelas Silver:
- `silver.dim_categorias`
- `silver.dim_paises`
- `silver.dim_cidades`
- `silver.dim_clientes`
- `silver.dim_funcionarios`
- `silver.dim_produtos`
- `silver.fato_vendas`

---

## 🧱 Modelagem Dimensional - Esquema em Floco de Neve

Nesta etapa do projeto, foi adotado o **modelo dimensional utilizando a abordagem em floco de neve** (*Snowflake Schema*). Esse modelo é uma variação do esquema estrela, em que as tabelas dimensão são normalizadas em múltiplas tabelas relacionadas. Isso permite uma melhor organização dos dados, elimina redundâncias e facilita a manutenção da base analítica.

### 📦 Tabela Fato

- **fato_vendas**: armazena os dados transacionais relacionados às vendas, como identificadores de cliente, produto, funcionário, informações de data, valor da venda, quantidade e descontos aplicados. Essa tabela representa os fatos (eventos de negócio) e concentra as métricas quantitativas para as análises.

### 🧩 Tabelas Dimensão (Normalizadas)

As dimensões foram modeladas de forma a reduzir a redundância e garantir uma estrutura mais limpa e modular:

- **dim_produtos**: contém os detalhes dos produtos, com chaves para categorias e atributos como classe, custo, resistência, validade e se causam alergia.
- **dim_categorias**: relacionada à dimensão de produtos, descreve as categorias dos itens vendidos.
- **dim_clientes**: armazena informações pessoais dos clientes e referências às cidades e países.
- **dim_funcionarios**: informações dos vendedores, incluindo datas importantes, gênero e localização (cidade e país).
- **dim_cidades**: representa as cidades envolvidas nas transações, ligando-se às tabelas de clientes e funcionários.
- **dim_paises**: contém os dados normalizados dos países e se relaciona com as cidades.

### 🧠 Benefícios do Modelo em Floco de Neve

- Redução de redundância nos dados dimensionais;
- Maior integridade e consistência entre entidades relacionadas;
- Estrutura mais organizada e normalizada, ideal para bases com alta granularidade geográfica e categórica;
- Suporte robusto para análises complexas e futuras expansões de dimensões.

Abaixo, o relacionamento entre essas tabelas é representado por um modelo de entidade-relacionamento (ER), que ilustra como as dimensões e a fato se conectam.


## 🧩 Modelo de Entidade-Relacionamento (Camada Silver)

A seguir, é apresentado o modelo de entidade-relacionamento construído a partir das tabelas da camada *Silver*, com base no processo de modelagem dimensional. Esse modelo define claramente as relações entre as tabelas de dimensão e a tabela fato, permitindo uma estrutura robusta para análises futuras.

### 📷 Diagrama MER

![Modelo de Entidade-Relacionamento](ER_SILVER.jpg)

> *Figura: Modelo de Entidade-Relacionamento.*



## 📚 Catálogo de Dados - Camada Silver

Abaixo está a descrição das tabelas e colunas que compõem o Data Lake na camada Silver, utilizando o formato Delta.

---

### 🧱 Tabela: `silver.dim_categorias`

| Coluna            | Tipo   | Descrição                                 |
|-------------------|--------|--------------------------------------------|
| id_categoria      | INT    | Chave primária da tabela de categorias     |
| descricao_categoria | STRING | Descrição da categoria                    |

---

### 🌍 Tabela: `silver.dim_paises`

| Coluna        | Tipo   | Descrição                               |
|---------------|--------|------------------------------------------|
| id_pais       | INT    | Chave primária da tabela de países       |
| descricao_pais| STRING | Nome completo do país                    |
| sigla_pais    | STRING | Código ou sigla do país                  |

---

### 🏙️ Tabela: `silver.dim_cidades`

| Coluna           | Tipo   | Descrição                                           |
|------------------|--------|------------------------------------------------------|
| id_cidade        | INT    | Chave primária da tabela de cidades                 |
| descricao_cidade | STRING | Nome da cidade                                      |
| codigo_postal    | INT    | Código postal da cidade                             |
| pais_id          | INT    | Chave estrangeira para a tabela de países           |
| descricao_pais   | STRING | Descrição do país (join com `dim_paises`)           |

---

### 👥 Tabela: `silver.dim_clientes`

| Coluna              | Tipo   | Descrição                                           |
|---------------------|--------|------------------------------------------------------|
| id_cliente          | INT    | Chave primária da tabela de clientes                |
| nome                | STRING | Primeiro nome do cliente                            |
| sigla_sobrenome     | STRING | Inicial do sobrenome do cliente                     |
| sobrenome           | STRING | Sobrenome do cliente                                |
| cidade_id           | INT    | Chave estrangeira para a cidade do cliente          |
| descricao_cidade    | STRING | Nome da cidade do cliente                           |
| descricao_pais      | STRING | Nome do país do cliente                             |

---

### 👨‍💼 Tabela: `silver.dim_funcionarios`

| Coluna              | Tipo   | Descrição                                           |
|---------------------|--------|------------------------------------------------------|
| id_funcionario      | INT    | Chave primária da tabela de funcionários            |
| nome                | STRING | Primeiro nome do funcionário                        |
| sigla_sobrenome     | STRING | Inicial do sobrenome do funcionário                 |
| sobrenome           | STRING | Sobrenome do funcionário                            |
| data_aniversario    | DATE   | Data de nascimento                                  |
| genero              | STRING | Gênero                                              |
| cidade_id           | INT    | Chave estrangeira para cidade do funcionário        |
| descricao_cidade    | STRING | Nome da cidade                                      |
| descricao_pais      | STRING | Nome do país                                        |
| data_contratacao    | DATE   | Data de contratação                                 |

---

### 📦 Tabela: `silver.dim_produtos`

| Coluna              | Tipo         | Descrição                                            |
|---------------------|--------------|-------------------------------------------------------|
| id_produto          | INT          | Chave primária da tabela de produtos                 |
| descricao           | STRING       | Descrição do produto                                 |
| custo               | DECIMAL(10,2)| Preço unitário do produto                            |
| id_categoria        | INT          | Chave estrangeira para categoria                     |
| categoria_produto   | STRING       | Descrição da categoria do produto                    |
| classe_produto      | STRING       | Classe do produto                                    |
| data_modificacao    | DATE         | Data da última modificação                           |
| resistencia         | STRING       | Resistência                                          |
| causa_alergia       | STRING       | Causa alergia?                                       |
| validade            | INT          | Dias de validade                                     |

---

### 🧾 Tabela: `silver.fato_vendas`

| Coluna             | Tipo         | Descrição                                         |
|--------------------|--------------|----------------------------------------------------|
| id_venda           | INT          | Chave primária da venda                           |
| id_vendedor        | INT          | Chave estrangeira para funcionário                |
| nome_vendedor      | STRING       | Nome completo do vendedor                         |
| id_cliente         | INT          | Chave estrangeira para cliente                    |
| nome_cliente       | STRING       | Nome completo do cliente                          |
| id_produto         | INT          | Chave estrangeira para produto                    |
| descricao_produto  | STRING       | Descrição do produto vendido                      |
| categoria_produto  | STRING       | Categoria do produto                              |
| custo              | DECIMAL(10,2)| Custo do produto                                   |
| quantidade         | INT          | Quantidade vendida                                |
| desconto           | DECIMAL(10,2)| Desconto aplicado                                 |
| valor_venda        | DECIMAL(10,2)| Valor total da venda com desconto                 |
| data_venda         | DATE         | Data da venda                                     |
| codigo_transacao   | STRING       | Número da transação                               |
### 

## 🗂️ Definição do Esquema das Tabelas

In [0]:
%sql
DROP DATABASE IF EXISTS silver CASCADE;
CREATE DATABASE IF NOT EXISTS silver;

USE silver;

CREATE TABLE IF NOT EXISTS dim_categorias (
    id_categoria INT COMMENT 'Chave primária da tabela de categorias',
    descricao_categoria STRING COMMENT 'Descrição da categoria'
) USING DELTA;

CREATE TABLE IF NOT EXISTS dim_paises (
    id_pais INT COMMENT 'Chave primária da tabela de países',
    descricao_pais STRING COMMENT 'Nome completo do país',
    sigla_pais STRING COMMENT 'Código ou sigla do país'
) USING DELTA;

CREATE TABLE IF NOT EXISTS dim_cidades (
    id_cidade INT COMMENT 'Chave primária da tabela de cidades',
    descricao_cidade STRING COMMENT 'Nome da cidade',
    codigo_postal INT COMMENT 'Código postal da cidade',
    pais_id INT COMMENT 'Chave estrangeira para a tabela de países',
    descricao_pais STRING COMMENT 'Descrição do país (join com dim_paises)'
) USING DELTA;

CREATE TABLE IF NOT EXISTS dim_clientes (
    id_cliente INT COMMENT 'Chave primária da tabela de clientes',
    nome STRING COMMENT 'Primeiro nome do cliente',
    sigla_sobrenome STRING COMMENT 'Inicial do sobrenome do cliente',
    sobrenome STRING COMMENT 'Sobrenome do cliente',
    cidade_id INT COMMENT 'Chave estrangeira para a cidade do cliente',
    descricao_cidade STRING COMMENT 'Nome da cidade do cliente',
    descricao_pais STRING COMMENT 'Nome do país do cliente'
) USING DELTA;

CREATE TABLE IF NOT EXISTS dim_funcionarios (
    id_funcionario INT COMMENT 'Chave primária da tabela de funcionários',
    nome STRING COMMENT 'Primeiro nome do funcionário',
    sigla_sobrenome STRING COMMENT 'Inicial do sobrenome do funcionário',
    sobrenome STRING COMMENT 'Sobrenome do funcionário',
    data_aniversario DATE COMMENT 'Data de nascimento',
    genero STRING COMMENT 'Gênero',
    cidade_id INT COMMENT 'Chave estrangeira para cidade do funcionário',
    descricao_cidade STRING COMMENT 'Nome da cidade',
    descricao_pais STRING COMMENT 'Nome do país',
    data_contratacao DATE COMMENT 'Data de contratação'
) USING DELTA;

CREATE TABLE IF NOT EXISTS dim_produtos (
    id_produto INT COMMENT 'Chave primária da tabela de produtos',
    descricao STRING COMMENT 'Descrição do produto',
    custo DECIMAL(10,2) COMMENT 'Preço unitário do produto',
    id_categoria INT COMMENT 'Chave estrangeira para categoria',
    categoria_produto STRING COMMENT 'Descrição da categoria do produto',
    classe_produto STRING COMMENT 'Classe do produto',
    data_modificacao DATE COMMENT 'Data da última modificação',
    resistencia STRING COMMENT 'Resistência',
    causa_alergia STRING COMMENT 'Causa alergia?',
    validade INT COMMENT 'Dias de validade'
) USING DELTA;

CREATE TABLE IF NOT EXISTS fato_vendas (
    id_venda INT COMMENT 'Chave primária da venda',
    id_vendedor INT COMMENT 'Chave estrangeira para funcionário',
    nome_vendedor STRING COMMENT 'Nome completo do vendedor',
    id_cliente INT COMMENT 'Chave estrangeira para cliente',
    nome_cliente STRING COMMENT 'Nome completo do cliente',
    id_produto INT COMMENT 'Chave estrangeira para produto',
    descricao_produto STRING COMMENT 'Descrição do produto vendido',
    categoria_produto STRING COMMENT 'Categoria do produto',
    custo DECIMAL(10,2) COMMENT 'Custo do produto',
    quantidade INT COMMENT 'Quantidade vendida',
    desconto DECIMAL(10,2) COMMENT 'Desconto aplicado',
    valor_venda DECIMAL(10,2) COMMENT 'Valor total da venda com desconto',
    data_venda DATE COMMENT 'Data da venda',
    codigo_transacao STRING COMMENT 'Número da transação'
) USING DELTA;

In [0]:
%sql
INSERT INTO dim_categorias
SELECT DISTINCT
    CAST(CategoryID AS INT),
    TRIM(CategoryName)
FROM bronze.raw_categorias
WHERE CategoryID IS NOT NULL;

INSERT INTO dim_paises
SELECT DISTINCT
  CAST(CountryID AS INT), 
  TRIM(CountryName),
  TRIM(CountryCode)
FROM bronze.raw_paises
WHERE CountryID IS NOT NULL;

INSERT INTO dim_cidades
SELECT DISTINCT
  CAST(C.CityID AS INT), 
  TRIM(C.CityName),
  CAST(C.Zipcode AS INT),
  CAST(C.CountryID AS INT),
  P.descricao_pais
FROM bronze.raw_cidades C
INNER JOIN silver.dim_paises P ON C.CountryID = P.id_pais
WHERE C.CityID IS NOT NULL;

INSERT INTO dim_clientes
SELECT DISTINCT
  CAST(CustomerID AS INT), 
  TRIM(FirstName),
  TRIM(MiddleInitial),
  TRIM(LastName),
  CAST(CityID AS INT),
  C.descricao_cidade,
  C.descricao_pais
FROM bronze.raw_clientes
INNER JOIN silver.dim_cidades C ON raw_clientes.CityID = C.id_cidade
WHERE CustomerID IS NOT NULL;

INSERT INTO dim_funcionarios
SELECT DISTINCT
  CAST(EmployeeID AS INT), 
  TRIM(FirstName),
  TRIM(MiddleInitial),
  TRIM(LastName),
  CAST(BirthDate AS DATE),
  TRIM(Gender),
  CAST(F.CityID AS INT),
  C.descricao_cidade,
  C.descricao_pais,
  CAST(HireDate AS DATE)
FROM bronze.raw_funcionarios F
INNER JOIN silver.dim_cidades C ON F.CityID = C.id_cidade
WHERE EmployeeID IS NOT NULL;

INSERT INTO dim_produtos
SELECT DISTINCT
  CAST(P.ProductID AS INT), 
  TRIM(P.ProductName),
  CAST(P.Price AS DECIMAL(10,2)),
  CAST(P.CategoryID AS INT),
  C.descricao_categoria,
  TRIM(P.Class),
  CAST(P.ModifyDate AS DATE),
  TRIM(P.Resistant),
  TRIM(P.IsAllergic),
  CAST(P.VitalityDays AS INT)
FROM bronze.raw_produtos P
INNER JOIN silver.dim_categorias C ON P.CategoryID = C.id_categoria
WHERE ProductID IS NOT NULL;

INSERT INTO fato_vendas
SELECT DISTINCT
  CAST(V.SalesID AS INT), 
  CAST(V.SalesPersonID AS INT),
  concat(F.nome, F.sobrenome),
  CAST(V.CustomerID AS INT),
  concat(C.nome, C.sobrenome),
  CAST(V.ProductID AS INT),
  P.descricao,
  P.categoria_produto, 
  CAST(P.custo AS DECIMAL(10,2)),
  CAST(V.Quantity AS INT),
  CAST(V.Discount AS DECIMAL(10,2)),
  (
    COALESCE(CAST(V.Quantity AS DECIMAL(10,2)), 0) * COALESCE(P.custo, 0)
    - COALESCE(CAST(V.Discount AS DECIMAL(10,2)), 0)
  ),
  CAST(V.SalesDate AS DATE),
  TRIM(V.TransactionNumber)
FROM bronze.raw_vendas V
INNER JOIN silver.dim_produtos P ON V.ProductID = P.id_produto
INNER JOIN silver.dim_clientes C ON V.CustomerID = C.id_cliente
INNER JOIN silver.dim_funcionarios F ON V.SalesPersonID = F.id_funcionario
WHERE SalesID IS NOT NULL 
AND SalesDate IS NOT NULL
AND (
    COALESCE(CAST(V.Quantity AS DECIMAL(10,2)), 0) * COALESCE(P.custo, 0)
    - COALESCE(CAST(V.Discount AS DECIMAL(10,2)), 0)
  ) > 0
;

num_affected_rows num_inserted_rows 6690208 6690208

In [0]:
silver_tables = {
    "dim_categorias": "Dimensão de Categorias de Produtos",
    "dim_cidades": "Dimensão de Cidades",
    "dim_clientes": "Dimensão de Clientes",
    "dim_funcionarios": "Dimensão de Funcionários",
    "dim_produtos": "Dimensão de Produtos",
    "dim_paises": "Dimensão de Países",
    "fato_vendas": "Fato de Vendas Realizadas"
}

for table, descricao in silver_tables.items():
    print(f"\n📘 Tabela Silver: {table} — {descricao}")
    display(spark.sql(f"SELECT * FROM silver.{table} LIMIT 10"))


📘 Tabela Silver: dim_categorias — Dimensão de Categorias de Produtos


id_categoria descricao_categoria 6 Seafood 7 Meat 4 Dairy 8 Grain 2 Shell fish 11 Produce 1 Confections 3 Cereals 9 Poultry 5 Beverages


📘 Tabela Silver: dim_cidades — Dimensão de Cidades


id_cidade descricao_cidade codigo_postal pais_id descricao_pais 74 Tampa 81280 32 United States 31 Wichita 93028 32 United States 24 Lincoln 95386 32 United States 37 Fresno 90795 32 United States 62 Mobile 78861 32 United States 2 Buffalo 17420 32 United States 29 Washington 63454 32 United States 67 Corpus Christi 78414 32 United States 72 Honolulu 93782 32 United States 91 Jacksonville 68274 32 United States


📘 Tabela Silver: dim_clientes — Dimensão de Clientes


...

id_produto descricao custo id_categoria categoria_produto classe_produto data_modificacao resistencia causa_alergia validade 46 Lambcasing 86.79 9 Poultry High 2017-07-12 Durable False 0 101 Soup - Campbells, Lentil 83.01 4 Dairy Medium 2018-02-19 Durable Unknown 99 193 Veal - Inside, Choice 60.53 11 Produce Medium 2017-02-26 Unknown False 19 335 Oil - Shortening,liqud, Fry 18.42 9 Poultry Low 2017-07-14 Weak Unknown 84 33 Beans - Wax 45.56 10 Snails Medium 2017-02-01 Weak True 0 159 Eggplant - Asian 92.11 7 Meat Medium 2017-12-29 Durable True 0 260 Yogurt - Blueberry, 175 Gr 26.89 7 Meat Low 2017-08-13 Durable False 31 365 Wine - Red, Harrow Estates, Cab 12.63 7 Meat Medium 2017-01-23 Weak True 95 135 Wiberg Super Cure 10.96 10 Snails Low 2018-04-25 Durable False 61 195 Beets - Mini Golden 3.52 2 Shell fish Medium 2017-08-18 Durable Unknown 70


📘 Tabela Silver: dim_paises — Dimensão de Países


id_pais descricao_pais sigla_pais 18 Czech Republic AF 29 Oman DZ 4 Uganda LV 72 Algeria NE 23 Saint Helena IN 108 Pakistan GB 159 Eritrea CX 3 Belize MK 140 Kuwait IT 21 Macedonia MA


📘 Tabela Silver: fato_vendas — Fato de Vendas Realizadas


id_venda id_vendedor nome_vendedor id_cliente nome_cliente id_produto descricao_produto categoria_produto custo quantidade desconto valor_venda data_venda codigo_transacao 202761 1 NicoleFuller 9305 QuentinLawson 94 V8 - Berry Blend Poultry 43.51 3 0.00 130.53 2018-01-06 PW3UA3LQ1XQ0I6GRIQZX 203753 14 WendiBuckley 54083 TammyPitts 219 Assorted Desserts Beverages 58.98 14 0.00 825.72 2018-04-25 MEKZGDP2KO6Z6EV341AY 203948 22 ToniaMc Millan 65571 AmberHolder 105 Ecolab - Mikroklene 4/4 L Confections 68.88 17 0.00 1170.96 2018-01-18 1A9HKNFH8WL59TR7ADL1 204427 19 BernardMoody 5483 JeremiahChambers 407 Pepsi - Diet, 355 Ml Meat 69.77 2 0.00 139.54 2018-01-24 04R9DAR19OZYKR9MCT8D 204542 11 SonyaDickson 73840 MonteMack 315 Wine - Gato Negro Cabernet Seafood 93.80 19 0.00 1782.20 2018-01-10 TDAASEM6ORQ088N1QYWA 204560 22 ToniaMc Millan 22490 DonnaReyes 90 Flavouring - Orange Poultry 69.32 6 0.00 415.92 2018-05-03 0A86TUOD569LF7MLUJPO 204640 23 JanetFlowers 59462 RebekahMontes 13 Water, Tap Produce 28.22 16 0.00 451.52 2018-01-02 FQNJ02T0M4S3C62Z8S7I 204650 7 ChadwickCook 44177 RandallRoberts 85 Cheese - Parmesan Cubes Meat 86.89 12 0.00 1042.68 2018-03-24 0SD9OMAELRQD0SFCWRD5 204940 18 WarrenBartlett 92224 FrankWade 310 Coffee - Dark Roast Poultry 79.98 24 0.00 1919.52 2018-04-23 QVNRMD5K2HL4PV0NU86P 205498 15 KariFinley 58434 BrandyMiles 255 Kellogs All Bran Bars Cereals 29.23 15 0.00 438.45 2018-05-03 2GY5HPESBCJRPGUVCQI4

# 🥇 Camada Gold – Dados Analíticos

> Camada voltada para consumo direto por dashboards, análises e relatórios. Aqui os dados são agregados, sumarizados e otimizados para performance.

### Tabelas Gold:
- `gold.vendas_resumo_mensal`
- `gold.compras_clientes_resumo_mensal`
- `gold.vendas_local`
- `gold.vendas_func`
- `gold.top_produtos`
- `gold.ultima_venda_produto`
- `gold.ticket_medio_produto`
- `gold.recencia_clientes`

---

## 📚 Catálogo de Dados – Camada Gold

---

### 📊 Tabela: `gold.vendas_resumo_mensal`
Resumo das vendas agregadas por ano e mês.

| Coluna            | Tipo        | Descrição                                      |
|-------------------|-------------|------------------------------------------------|
| ano               | INT         | Ano da venda                                   |
| mes               | INT         | Mês da venda                                   |
| total_vendas      | DECIMAL     | Valor total das vendas no mês                  |
| media_vendas      | DECIMAL     | Valor médio das vendas no mês                  |
| clientes_unicos   | INT         | Quantidade de clientes únicos no período       |
| qtd_vendas        | INT         | Total de registros de vendas no período        |

---

### 📊 Tabela: `gold.compras_clientes_resumo_mensal`
Resumo mensal de compras por cliente.

| Coluna                   | Tipo        | Descrição                                      |
|--------------------------|-------------|------------------------------------------------|
| id_cliente               | INT         | Identificador do cliente                       |
| nome_cliente             | STRING      | Nome completo do cliente                       |
| ano                      | INT         | Ano da compra                                  |
| mes                      | INT         | Mês da compra                                  |
| total_compras            | INT         | Total de compras realizadas                    |
| qtd_itens_comprados      | INT         | Quantidade total de itens comprados            |
| valor_total              | DECIMAL     | Valor total gasto                              |
| desconto_total           | DECIMAL     | Total de desconto obtido                       |

---

### 📊 Tabela: `gold.vendas_local`
Resumo das vendas por localização.

| Coluna            | Tipo        | Descrição                                      |
|-------------------|-------------|------------------------------------------------|
| descricao_cidade  | STRING      | Nome da cidade                                 |
| descricao_pais    | STRING      | Nome do país                                   |
| vendas_totais     | DECIMAL     | Valor total de vendas na localidade            |

---

### 📊 Tabela: `gold.vendas_func`
Resumo de vendas por funcionário.

| Coluna              | Tipo        | Descrição                                      |
|---------------------|-------------|------------------------------------------------|
| id_vendedor         | INT         | Identificador do funcionário                   |
| nome_vendedor       | STRING      | Nome do funcionário                            |
| total_vendas        | DECIMAL     | Valor total vendido                            |
| total_descontos     | DECIMAL     | Total de descontos concedidos                  |
| total_itens         | INT         | Quantidade total de itens vendidos             |

---

### 📊 Tabela: `gold.top_produtos`
Produtos com maior volume de vendas.

| Coluna              | Tipo        | Descrição                                      |
|---------------------|-------------|------------------------------------------------|
| id_produto          | INT         | Identificador do produto                       |
| descricao_produto   | STRING      | Nome do produto                                |
| categoria_produto   | STRING      | Categoria do produto                           |
| qtd_vendida         | INT         | Quantidade total vendida                       |
| valor_total         | DECIMAL     | Valor total gerado                             |

---

### 📊 Tabela: `gold.ultima_venda_produto`
Data da última venda por produto.

| Coluna              | Tipo        | Descrição                                      |
|---------------------|-------------|------------------------------------------------|
| id_produto          | INT         | Identificador do produto                       |
| descricao_produto   | STRING      | Nome do produto                                |
| ultima_venda        | DATE        | Data da última venda registrada                |

---

### 📊 Tabela: `gold.ticket_medio_produto`
Ticket médio por produto.

| Coluna              | Tipo        | Descrição                                      |
|---------------------|-------------|------------------------------------------------|
| id_produto          | INT         | Identificador do produto                       |
| descricao_produto   | STRING      | Nome do produto                                |
| ticket_medio        | DECIMAL     | Valor médio por venda do produto               |

---

### 📊 Tabela: `gold.recencia_clientes`
Dias desde a última compra por cliente.

| Coluna                    | Tipo        | Descrição                                      |
|---------------------------|-------------|------------------------------------------------|
| id_cliente                | INT         | Identificador do cliente                       |
| nome_cliente              | STRING      | Nome do cliente                                |
| ultima_compra             | DATE        | Data da última compra                          |
| dias_desde_ultima_compra | INT         | Dias desde a última compra                     |

---


## 🗂️ Criação das tabelas gold

In [0]:
from pyspark.sql.functions import (
    year, month, sum as _sum, avg, countDistinct, col, round, max as _max, datediff, current_date
)

spark.sql("DROP DATABASE IF EXISTS gold CASCADE")
spark.sql("CREATE DATABASE IF NOT EXISTS gold")

df_vendas = spark.table("silver.fato_vendas")
df_clientes = spark.table("silver.dim_clientes")

In [0]:
df_resumo = df_vendas \
    .withColumn("ano", year("data_venda")) \
    .withColumn("mes", month("data_venda")) \
    .groupBy("ano", "mes") \
    .agg(
        countDistinct("id_venda").alias("qtd_vendas"),
        _sum("quantidade").alias("qtd_itens_vendidos"),
        _sum("valor_venda").alias("valor_total"),
        _sum("desconto").alias("desconto_total"),
        round((_sum("valor_venda") / countDistinct("id_venda")), 2).alias("ticket_medio")
    ) \
    .orderBy("ano", "mes")

df_resumo.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.vendas_resumo_mensal")


In [0]:
df_clientes_ativos = df_vendas \
    .withColumn("ano", year("data_venda")) \
    .withColumn("mes", month("data_venda")) \
    .groupBy("id_cliente", "nome_cliente", "ano", "mes") \
    .agg(
        countDistinct("id_venda").alias("total_compras"),
        _sum("quantidade").alias("qtd_itens_comprados"),
        _sum("valor_venda").alias("valor_total"),
        _sum("desconto").alias("desconto_total")
    ) \
    .orderBy(col("total_compras").desc())

df_clientes_ativos.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.compras_clientes_resumo_mensal")

In [0]:
df_ticket_medio = df_vendas \
    .groupBy("id_produto", "descricao_produto") \
    .agg(
        (_sum("valor_venda") / _sum("quantidade")).alias("ticket_medio"),
        _sum("quantidade").alias("qtd_total_vendida")
    ) \
    .orderBy(col("ticket_medio").desc())

df_ticket_medio.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.ticket_medio_produto")

In [0]:
from pyspark.sql.functions import datediff, to_date, lit, col

df_recencia = df_vendas.groupBy("id_cliente", "nome_cliente") \
    .agg(_max("data_venda").alias("ultima_compra"))

# Simula a data de referência como se estivéssemos analisando em 2018-06-01
# Isso é necessário porque os dados de venda são todos antigos (até 2018-05-09),
# e usar a data atual (2025) distorce as análises de recência, resultando em valores iguais.
df_recencia = df_recencia.withColumn(
    "dias_desde_ultima_compra",
    datediff(lit("2018-06-01"), col("ultima_compra"))
)
df_recencia.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.recencia_clientes")

In [0]:
df_ult_venda = df_vendas.groupBy("id_produto", "descricao_produto") \
    .agg(_max("data_venda").alias("ultima_compra"))

df_ult_venda = df_ult_venda.withColumn("dias_desde_ultima_compra", datediff(current_date(), col("ultima_compra")))
df_ult_venda.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.ultima_venda_produto")

In [0]:
df_top_produtos = df_vendas.groupBy("id_produto", "descricao_produto") \
    .agg(
        _sum("quantidade").alias("qtd_total"),
        _sum("valor_venda").alias("vendas_totais"),
        _sum("desconto").alias("desconto_total")
    ) \
    .orderBy(col("vendas_totais").desc())

df_top_produtos.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.top_produtos")

In [0]:
df_vendas_local = df_vendas \
    .join(df_clientes.select("id_cliente", "descricao_cidade", "descricao_pais"), on="id_cliente", how="left") \
    .groupBy("descricao_cidade", "descricao_pais") \
    .agg(_sum("valor_venda").alias("vendas_totais"))

df_vendas_local.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.vendas_local")

In [0]:
df_vendas_func = df_vendas.groupBy("id_vendedor", "nome_vendedor") \
    .agg(
        _sum("valor_venda").alias("total_vendas"),
        countDistinct("id_cliente").alias("clientes_atendidos"),
        countDistinct("id_venda").alias("total_transacoes")
    )
df_vendas_func.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("gold.vendas_func")

In [0]:
print("📊 Tabela: Vendas Resumo Mensal")
display(spark.sql("SELECT * FROM gold.vendas_resumo_mensal"))

print("📊 Tabela: Compras Clientes Resumo Mensal")
display(spark.sql("SELECT * FROM gold.compras_clientes_resumo_mensal"))

print("📊 Tabela: Vendas por Localidade (Cidade e País)")
display(spark.sql("SELECT * FROM gold.vendas_local"))

print("📊 Tabela: Vendas por Funcionário")
display(spark.sql("SELECT * FROM gold.vendas_func"))

print("📊 Tabela: Top Produtos Vendidos")
display(spark.sql("SELECT * FROM gold.top_produtos"))

print("📊 Tabela: Última Venda por Produto")
display(spark.sql("SELECT * FROM gold.ultima_venda_produto"))

print("📊 Tabela: Ticket Médio por Produto")
display(spark.sql("SELECT * FROM gold.ticket_medio_produto"))

print("📊 Tabela: Recência de Clientes")
display(spark.sql("SELECT * FROM gold.recencia_clientes"))

📊 Tabela: Vendas Resumo Mensal


ano mes qtd_vendas qtd_itens_vendidos valor_total desconto_total ticket_medio 2018 1 1606967 20900232 1062437807.11 48136.50 661.14 2018 2 1451286 18862624 957843386.05 43376.90 660.00 2018 3 1609089 20930695 1064054127.28 48282.30 661.28 2018 4 1555995 20229236 1028112185.77 46639.40 660.74 2018 5 466871 6079750 309095633.51 13978.30 662.06

📊 Tabela: Compras Clientes Resumo Mensal


id_cliente nome_cliente ano mes total_compras qtd_itens_comprados valor_total desconto_total 25402 DonaldGarcia 2018 3 40 280 14938.63 0.70 24818 TyroneRiley 2018 4 39 273 14401.78 1.70 19007 KathyHuang 2018 3 38 190 7709.95 1.20 46820 DionFuentes 2018 1 37 444 20344.22 1.30 84711 StaciCohen 2018 1 37 814 40613.10 1.10 94000 MarciaAlexander 2018 3 37 888 44054.32 2.00 14460 JoeyBuchanan 2018 3 37 148 6826.88 1.40 97863 RondaWallace 2018 1 37 925 55142.75 1.00 33436 BettyKing 2018 4 36 324 12740.51 0.70 51766 ArleneJennings 2018 1 36 504 25405.64 1.00 17448 StacieDuke 2018 3 36 180 7450.35 1.30 21422 CristinaBarajas 2018 2 35 210 12105.42 0.90 18175 ChasityGraham 2018 2 35 175 7477.25 1.10 10470 JulioWard 2018 4 35 105 4999.50 0.60 3146 GeoffreyEstes 2018 1 35 35 1916.21 0.60 39155 GeoffreySparks 2018 3 35 350 20609.20 1.00 76552 DeanaPham 2018 1 35 700 34327.90 1.10 95495 OliviaWise 2018 3 35 875 44264.60 0.90 67117 TamiHanson 2018 2 35 595 31012.64 0.80 75643 GuadalupeOliver 2018 3 34 680 35438.40 1.20 59225 BennyCannon 2018 3 34 510 26736.20 0.70 70044 NatashaRubio 2018 1 34 612 30380.56 1.10 46720 TerrenceCampbell 2018 4 34 408 20354.74 1.10 61264 CarlosAtkins 2018 2 34 544 25483.46 1.50 65983 DewayneWalsh 2018 1 34 578 30331.53 1.40 29918 WallaceJimenez 2018 4 34 272 14939.22 1.10 39131 CarltonCardenas 2018 4 33 330 18632.10 1.00 74743 GarrettSchaefer 2018 3 33 627 30342.20 0.80 14005 ConstancePace 2018 3 33 132 5993.52 2.00 32994 AmyNoble 2018 1 33 297 14850.84 1.50 51768 DonaldHouston 2018 3 33 462 24397.10 0.70 59358 HeatherBishop 2018 1 33 528 29240.18 1.10 37604 KristinaCannon 2018 3 33 330 17270.70 0.80 34503 DemetriusMc Neil 2018 1 33 297 14482.65 0.60 66768 RodolfoPeters 2018 4 33 561 30785.38 0.60 24965 IsmaelWiggins 2018 1 33 231 12227.83 1.10 28628 SaulVelazquez 2018 1 33 264 13697.40 1.80 62678 BradleyLin 2018 4 33 528 24134.72 0.80 22669 TamiCruz 2018 4 33 198 11667.52 0.80 81337 AshleyCook 2018 1 33 693 32144.56 1.40 63715 GeoffreyLawson 2018 1 33 561 28859.22 1.00 89629 SusanBurnett 2018 4 33 759 40578.19 1.40 36592 AntoineFisher 2018 3 33 330 17747.00 1.40 95157 PaulaLin 2018 1 33 825 40856.00 1.00 75926 CedricMendoza 2018 1 33 660 39092.40 0.80 37267 MistiBenson 2018 4 33 330 16602.50 1.30 83334 MiguelRoss 2018 4 33 726 36636.94 1.20 93091 JaimeShannon 2018 3 33 792 43426.84 1.40 23216 DevonKaufman 2018 2 33 198 11324.74 0.80 53581 BryceBird 2018 4 33 462 21261.82 1.80 40884 GilbertoPhelps 2018 1 33 363 18812.45 1.40 64922 JessieBeard 2018 1 33 561 29763.42 1.20 25860 VickyMeadows 2018 4 33 231 12122.80 0.50 59801 KevinWade 2018 3 32 512 26821.08 1.80 24545 EdgarAbbott 2018 1 32 224 10563.26 1.00 52343 EstherWaller 2018 3 32 448 22949.04 0.60 78102 AprilSnow 2018 3 32 640 33430.90 0.50 77647 DamianRoman 2018 3 32 640 34287.50 1.10 6001 ByronCarr 2018 1 32 64 3552.66 0.40 19019 CandiceKeith 2018 1 32 160 8734.60 1.10 17431 StacieLang 2018 1 32 160 7464.30 1.10 85734 JosephValenzuela 2018 1 32 704 39448.90 1.50 92140 JoseChapman 2018 1 32 768 44237.96 1.00 68404 LloydRandall 2018 2 32 576 26296.72 1.10 78259 CherylSheppard 2018 4 32 640 33755.80 1.40 14839 RobertoSherman 2018 1 32 128 4997.22 1.10 29294 PriscillaRandall 2018 1 32 256 11187.76 0.80 27762 TerriHarding 2018 3 32 256 11841.32 1.00 16080 KristinaJensen 2018 1 32 160 7325.40 1.20 36550 AnnaFrazier 2018 3 32 320 18181.10 0.70 75265 WendiSpears 2018 4 32 640 30332.00 0.60 26798 SherrieLarsen 2018 1 32 224 11911.20 1.40 7191 JerryCastro 2018 3 32 64 3605.82 1.40 89495 CamilleGoodman 2018 1 32 736 40062.80 0.90 90697 BryceVasquez 2018 3 32 736 41095.67 0.50 3291 LloydWilson 2018 3 32 32 1720.15 0.80 33456 JesseBenton 2018 1 32 288 15531.81 1.20 7943 WarrenSalas 2018 2 32 96 4248.79 0.20 45782 GarryHoover 2018 1 32 384 23263.60 1.40 35658 SherriHarris 2018 3 32 320 15255.70 0.80 60141 CecilWebster 2018 3 32 512 25398.40 0.80 24278 JoniBarry 2018 3 32 224 9115.44 1.50 69301 KurtSimpson 2018 4 32 576 28110.98 0.70 76081 SheilaSalazar 2018 1 32 640 27533.

📊 Tabela: Vendas por Localidade (Cidade e País)


...

id_produto descricao_produto ultima_compra dias_desde_ultima_compra 124 Macaroons - Two Bite Choc 2018-05-09 2530 366 Tahini Paste 2018-05-09 2530 51 Wine - Crozes Hermitage E. 2018-05-09 2530 223 Pail With Metal Handle 16l White 2018-05-09 2530 386 Sprouts - Baby Pea Tendrils 2018-05-09 2530 189 Bread - Roll, Soft White Round 2018-05-09 2530 248 Beef - Inside Round 2018-05-09 2530 147 Cheese - Mozzarella 2018-05-09 2530 422 Garlic - Primerba, Paste 2018-05-09 2530 331 Cookies Cereal Nut 2018-05-09 2530 121 Muffin Batt - Blueberry Passion 2018-05-09 2530 270 Cheese Cloth No 100 2018-05-09 2530 257 Pasta - Detalini, White, Fresh 2018-05-09 2530 198 Lime Cordial - Roses 2018-05-09 2530 283 Bread Fig And Almond 2018-05-09 2530 249 Cookie Dough - Double 2018-05-09 2530 307 Foam Cup 6 Oz 2018-05-09 2530 185 Foam Dinner Plate 2018-05-09 2530 396 Tea - Jasmin Green 2018-05-09 2530 58 Dc Hikiage Hira Huba 2018-05-09 2530 251 Oranges - Navel, 72 2018-05-09 2530 171 Gloves - Goldtouch Disposable 2018-05-09 2530 179 Yoghurt Tubes 2018-05-09 2530 24 Beer - Alexander Kieths, Pale Ale 2018-05-09 2530 36 Table Cloth 54x72 White 2018-05-09 2530 97 Veal - Inside 2018-05-09 2530 342 Mangoes 2018-05-09 2530 389 Pomello 2018-05-09 2530 313 Veal - Slab Bacon 2018-05-09 2530 146 Bananas 2018-05-09 2530 191 Hickory Smoke, Liquid 2018-05-09 2530 304 Banana Turning 2018-05-09 2530 132 Beer - Blue 2018-05-09 2530 202 Bay Leaf 2018-05-09 2530 445 Pastry - Choclate Baked 2018-05-09 2530 4 Sauce - Gravy, Au Jus, Mix 2018-05-09 2530 106 Pickerel - Fillets 2018-05-09 2530 260 Yogurt - Blueberry, 175 Gr 2018-05-09 2530 27 Chocolate - Compound Coating 2018-05-09 2530 113 Ocean Spray - Kiwi Strawberry 2018-05-09 2530 221 Bread Crumbs - Panko 2018-05-09 2530 103 Cream Of Tartar 2018-05-09 2530 240 Wine - Chablis 2003 Champs 2018-05-09 2530 268 Vanilla Beans 2018-05-09 2530 309 Muffin Batt - Choc Chk 2018-05-09 2530 34 Mustard Prepared 2018-05-09 2530 108 Pasta - Orecchiette 2018-05-09 2530 16 Kellogs Special K Cereal 2018-05-09 2530 321 Potatoes - Instant, Mashed 2018-05-09 2530 243 Sun - Dried Tomatoes 2018-05-09 2530 19 Tea - Earl Grey 2018-05-09 2530 139 Chicken - Wieners 2018-05-09 2530 439 Beef - Chuck, Boneless 2018-05-09 2530 93 Bandage - Fexible 1x3 2018-05-09 2530 194 Lettuce - Frisee 2018-05-09 2530 408 Blueberries 2018-05-09 2530 395 Juice - Lime 2018-05-09 2530 339 Beef - Striploin Aa 2018-05-09 2530 230 Wine - Cahors Ac 2000, Clos 2018-05-09 2530 94 V8 - Berry Blend 2018-05-09 2530 76 Wine - Fume Blanc Fetzer 2018-05-09 2530 372 Wine - Two Oceans Cabernet 2018-05-09 2530 204 Scallop - St. Jaques 2018-05-09 2530 164 Loquat 2018-05-09 2530 305 Pastry - Cheese Baked Scones 2018-05-09 2530 360 Wine - Hardys Bankside Shiraz 2018-05-09 2530 369 Rambutan 2018-05-09 2530 25 Soupcontfoam16oz 116con 2018-05-09 2530 349 Puree - Mocha 2018-05-09 2530 130 Beef Wellington 2018-05-09 2530 184 Hersey Shakes 2018-05-09 2530 62 Pears - Bosc 2018-05-09 2530 314 Salmon Steak - Cohoe 8 Oz 2018-05-09 2530 310 Coffee - Dark Roast 2018-05-09 2530 87 Wine - Pinot Noir Latour 2018-05-09 2530 133 Beef - Top Sirloin - Aaa 2018-05-09 2530 261 Chinese Foods - Chicken 2018-05-09 2530 48 Pecan Raisin - Tarts 2018-05-09 2530 57 Sausage - Breakfast 2018-05-09 2530 214 French Pastry - Mini Chocolate 2018-05-09 2530 353 Milk Powder 2018-05-09 2530 429 Beef - Short Loin 2018-05-09 2530 315 Wine - Gato Negro Cabernet 2018-05-09 2530 226 Chestnuts - Whole,canned 2018-05-09 2530 17 Wine - White, Mosel Gold 2018-05-09 2530 88 Remy Red 2018-05-09 2530 425 Wine - Redchard Merritt 2018-05-09 2530 401 Tart Shells - Sweet, 4 2018-05-09 2530 382 Soup - Campbells Bean Medley 2018-05-09 2530 66 Pie Filling - Cherry 2018-05-09 2530 229 Bread - Hot Dog Buns 2018-05-09 2530 236 Tomato - Tricolor Cherry 2018-05-09 2530 45 Beef - Ground Medium 2018-05-09 2530 319 Towels - Paper / Kraft 2018-05-09 2530 136 Vol Au Vents 2018-05-09 2530 14 Beef - Top Sirloin 2018-05-09 2530 384 Fond - Neutral 2018-05-09 

📊 Tabela: Ticket Médio por Produto


id_produto descricao_produto ticket_medio qtd_total_vendida 98 Shrimp - 31/40 99.87771077026093870974 191156 248 Beef - Inside Round 99.31756401354739202103 188671 392 Puree - Passion Fruit 98.82774862980345838643 193038 345 Bread - Calabrese Baguette 98.59772030955096696316 195509 149 Zucchini - Yellow 98.45767935342271966048 192274 104 Tia Maria 98.24764708305230477740 194227 268 Vanilla Beans 97.83765372670807453416 193200 328 Tuna - Salad Premix 96.87766996871741397289 191800 217 Bread - Multigrain 96.51761839870856831380 190796 32 Lettuce - Treviso 96.40769422421219327250 193861 201 Grenadine 96.38771954586664468804 194128 351 Hot Chocolate - Individual 96.07768522885681644289 190818 144 Placemat - Scallop, White 95.78770505935997174818 192554 298 Pop Shoppe Cream Soda 95.73774164454866390084 194035 199 Pork - Hock And Feet Attached 95.73763024320368698035 192678 256 Soup Knorr Chili With Beans 95.69768793660723595037 191820 413 Ice Cream Bar - Oreo Cone 95.40771412975750928200 194193 10 Scampi Tail 95.09772192896404602856 192663 347 Pail For Lid 1537 94.62769196905854977674 190812 223 Pail With Metal Handle 16l White 94.43772995930664379191 191186 244 Beef - Rib Eye Aaa 94.06775004227257355428 189248 80 Wasabi Powder 93.97771308246731478377 190912 315 Wine - Gato Negro Cabernet 93.79775413464751085867 191552 151 Mushrooms - Black, Dried 93.55765977758856464639 193785 451 Soup - Campbells Tomato Ravioli 93.53773040502654236560 190827 284 Beer - Rickards Red 93.48770857875049083432 193548 53 Cassis 92.62778892478899264541 191581 418 Truffle Cups - Brown 92.24768137544121148133 193218 159 Eggplant - Asian 92.10770699914405634791 193938 226 Chestnuts - Whole,canned 92.08769565842733567569 194676 88 Remy Red 91.99772712976747111735 190772 395 Juice - Lime 91.77769321827980436747 192606 175 Oil - Safflower 91.76771604682052133488 192736 2 Cookie Chocolate Chip With 91.22768073199453922069 191914 279 Beef - Texas Style Burger 91.17766826304135125393 194190 305 Pastry - Cheese Baked Scones 91.09767033567771575152 190242 378 Bread Foccacia Whole 90.78769930610698512048 192681 84 Peas - Frozen 90.29773661384229009917 193913 341 Bread - Roll, Canadian Dinner 90.25769714904968322774 191936 215 Veal - Brisket, Provimi,bnls 90.11766300282579787234 192512 443 Lettuce - Spring Mix 90.01764549834592457835 190741 8 Halibut - Steaks 89.85768323984185796195 193244 406 Shrimp - Baby, Warm Water 89.79769059616176248365 191911 379 Smoked Paprika 89.29772705733691359975 189930 24 Beer - Alexander Kieths, Pale Ale 89.03773144960473796742 193163 274 Papayas 88.11781293819719135221 191124 308 Tea - Decaf Lipton 88.11766924956083970521 195259 324 Apricots - Dried 87.89773473525101237317 195827 69 Raspberries - Fresh 87.60771302121933656065 190251 369 Rambutan 87.17763064806781018488 194779 349 Puree - Mocha 86.90769752736287052793 190404 85 Cheese - Parmesan Cubes 86.88772101751459549625 191840 46 Lambcasing 86.78767115880324021818 190481 81 Cookies - Assorted 86.64764858589358390261 193373 419 Pork - Belly Fresh 86.12768358492318169155 193834 380 Wine - White Cab Sauv.on 85.96773955976560688130 194033 20 Chocolate - Feathers 85.89767326707139062395 193877 424 Vinegar - Tarragon 85.87770006431935597651 192788 236 Tomato - Tricolor Cherry 85.68776941849439634402 192999 218 Barramundi 85.18769025380919981031 194004 68 Beets - Candy Cane, Organic 84.87771148578986284536 192046 358 Cheese - Boursin, Garlic / Herbs 84.70762288497648979007 195447 416 Baking Powder 84.67768379787365050696 194888 257 Pasta - Detalini, White, Fresh 84.43768143419033503197 190937 9 Rabbit - Whole 84.41770584786982904764 189351 312 Salmon - Sockeye Raw 84.05771549582995633873 191245 137 Wine - White, Schroder And Schyl 84.05768617638713338664 193835 179 Yoghurt Tubes 83.87777803647259493959 197573 437 Chips Potato All Dressed - 43g 83.58771104980097210504 193189 426 Scallops - Live In Shell 83.57770210193306961448 191871 230 Wine - Cahors Ac 2000, Clos 83.53773388751622764772

📊 Tabela: Recência de Clientes


id_cliente nome_cliente ultima_compra dias_desde_ultima_compra 82088 CrystalGregory 2018-05-09 2530 33291 ShadCannon 2018-05-07 2532 28032 FrancisWaters 2018-05-05 2534 20135 AllanBradford 2018-05-09 2530 41089 HectorGould 2018-04-30 2539 61036 NormaLynch 2018-05-08 2531 12472 JennieLeon 2018-05-05 2534 76805 JessRubio 2018-05-08 2531 43898 TimMorris 2018-05-07 2532 39727 TaniaValentine 2018-05-08 2531 13856 AmberNeal 2018-05-07 2532 82065 TanyaBlake 2018-05-01 2538 70419 AllysonBerry 2018-05-05 2534 9643 SuzanneBlackwell 2018-05-09 2530 6691 JeromeMooney 2018-05-07 2532 16397 FernandoHiggins 2018-05-09 2530 19853 TimRubio 2018-05-06 2533 6606 GeneWoods 2018-05-09 2530 62953 CrystalTate 2018-05-07 2532 18746 AaronWatson 2018-05-08 2531 67064 CecilSavage 2018-05-01 2538 38933 AmandaAnthony 2018-05-07 2532 88849 GretchenWilkinson 2018-05-08 2531 57993 SonyaGalloway 2018-05-08 2531 6276 LydiaDennis 2018-05-07 2532 86369 WarrenFrye 2018-05-06 2533 4814 TheodoreBond 2018-05-08 2531 63335 JohnPaul 2018-05-03 2536 35912 JoanLynn 2018-05-06 2533 65247 TerrySummers 2018-05-08 2531 72868 JoycePham 2018-05-09 2530 52971 MonteQuinn 2018-05-06 2533 61820 BryceHerring 2018-05-07 2532 84091 MarkMcclain 2018-05-07 2532 20025 ChristineLittle 2018-05-09 2530 87886 AlfonsoHancock 2018-05-09 2530 40353 SamanthaBrady 2018-05-07 2532 47789 TeraShaffer 2018-05-02 2537 12433 JanineSpears 2018-05-06 2533 94442 AliciaRowland 2018-05-07 2532 16038 AlisonByrd 2018-05-09 2530 25132 FaithEnglish 2018-05-08 2531 97210 MichealPerry 2018-05-09 2530 37825 ChrystalLane 2018-05-09 2530 74246 NathanBallard 2018-05-09 2530 44358 LanceCowan 2018-05-09 2530 39597 OmarButler 2018-05-08 2531 96271 AbrahamWarner 2018-05-09 2530 6002 RhondaAndersen 2018-05-09 2530 65513 CharityCampbell 2018-05-03 2536 15682 AlejandroMontgomery 2018-05-08 2531 12754 VivianLin 2018-05-09 2530 69286 DionTodd 2018-05-07 2532 63583 CameronYu 2018-05-08 2531 325 JeannieDalton 2018-05-06 2533 93204 RebekahMiranda 2018-05-08 2531 79699 MichelleLarsen 2018-05-09 2530 91984 ShelleyDixon 2018-05-09 2530 85678 AngieVasquez 2018-05-08 2531 95889 MarisolCarrillo 2018-05-08 2531 20022 TimHall 2018-05-09 2530 5912 TyValenzuela 2018-05-08 2531 5499 ClaudeMonroe 2018-05-09 2530 94908 EricCooke 2018-05-08 2531 43334 SamuelRowe 2018-05-07 2532 69498 SusanaMccarty 2018-05-06 2533 97330 KenyaHeath 2018-05-07 2532 66314 IraOsborn 2018-05-05 2534 95941 JoleneEaton 2018-05-08 2531 7849 TanyaBauer 2018-05-08 2531 59421 CourtneyMosley 2018-05-07 2532 69798 SherylTrevino 2018-05-09 2530 71745 WendiBowen 2018-05-08 2531 75374 TimMelton 2018-05-08 2531 3053 LatoyaKirby 2018-05-08 2531 73299 JackFry 2018-05-09 2530 44001 ToniaEnglish 2018-05-08 2531 71566 AntonioBarber 2018-05-08 2531 75190 RoseJones 2018-05-08 2531 24229 BenShelton 2018-05-09 2530 79109 BartHorn 2018-05-09 2530 31003 ArnoldHorne 2018-05-09 2530 91198 NathanielDavies 2018-05-07 2532 58208 JoannaFisher 2018-05-04 2535 10359 DemetriusGibbs 2018-05-09 2530 78690 MorganHughes 2018-05-07 2532 77299 OtisBright 2018-05-09 2530 40217 DonovanCooper 2018-05-09 2530 87662 IsabelAguirre 2018-05-08 2531 6988 JuanWebster 2018-05-08 2531 50917 CariTorres 2018-05-08 2531 52274 DionMc Cormick 2018-05-09 2530 43343 GuyPerkins 2018-04-30 2539 62875 JessieStark 2018-05-09 2530 88767 HerbertSantiago 2018-05-04 2535 82293 ClayHaas 2018-04-30 2539 40956 LeonardUnderwood 2018-05-06 2533 17116 KerryAlvarado 2018-05-09 2530 34007 DarnellLuna 2018-05-08 2531 17600 DarcyHarper 2018-05-09 2530 21955 ClintonHood 2018-05-09 2530 54559 ShaneKane 2018-05-09 2530 91229 SonjaVillegas 2018-05-08 2531 58243 RubenCarey 2018-05-07 2532 87352 SamanthaHancock 2018-05-08 2531 9148 JamiLane 2018-05-09 2530 41848 StephanRose 2018-05-06 2533 2563 JohannaYu 2018-05-09 2530 41894 SethChan 2018-05-06 2533 25566 AllisonBlake 2018-05-04 2535 37357 SherriMac Donald 2018-05-09 2530 79880 AnnLucas 2018-05-09 2530 84596 DeborahLove 2018-05-04 2535 91796 LucasMullen 2018-05-09 2530 63673 WillieWinters 20

# 📊 Análise dos Dados de Vendas

Nesta seção, apresentamos uma análise detalhada dos dados coletados e processados, com foco nas informações mais relevantes sobre clientes, produtos, vendas e vendedores. A análise será dividida em categorias específicas para melhor compreensão e tomada de decisões estratégicas.

## 1. 🛍️ Análise do Comportamento de Compra dos Clientes

A primeira parte da análise se concentra no comportamento dos clientes, abordando aspectos como a **recência** das compras, o **ticket médio** por produto, e o **total de compras** realizadas. Entender esses fatores ajuda a segmentar os clientes com base no seu nível de engajamento e identificar oportunidades de aumentar o valor médio das compras.

- **Clientes mais ativos**: Identificação dos clientes que realizaram o maior número de compras.
- **Ticket médio**: Cálculo da média do valor gasto por cliente em suas compras.

## 2. 📅 Análise de Vendas por Período (Ano e Mês)

Nesta análise, exploramos a performance de vendas ao longo do tempo, segmentando as vendas por **ano e mês**. Esse tipo de análise permite identificar **tendências sazonais**, avaliar a **crescimento das vendas** e realizar comparações entre os diferentes períodos.

- **Vendas por mês e ano**: Determinação do total de vendas em cada mês, permitindo observar picos de vendas e períodos de queda.

## 3. 🌍 Análise de Vendas por Localidade

Analisamos as vendas por **cidade** e **país**, destacando as regiões com maior volume de vendas. Com essas informações, é possível realizar decisões sobre a **distribuição geográfica dos produtos** e identificar mercados potenciais para expansão.

- **Vendas por cidade**: Identificação das cidades com o maior volume de vendas.
- **Vendas por país**: Determinação dos países com os maiores índices de vendas.

## 4. 👩‍💼 Análise de Performance dos Vendedores

Essa análise se concentra na **performance de vendas de cada vendedor**, comparando o total vendido por cada um. Essa informação é útil para reconhecer os vendedores de maior desempenho e aqueles que podem precisar de mais treinamento ou motivação.

- **Top vendedores**: Identificação dos vendedores que mais geraram vendas.

## 5. 🛒 Análise dos Produtos Mais Vendidos

Aqui, analisamos os **produtos mais vendidos**, com destaque para aqueles que geram o maior volume de receita. Com essa análise, é possível identificar quais itens devem receber mais foco em campanhas promocionais ou na gestão de estoque.

- **Produtos com maior volume de vendas**: Determinação dos produtos que mais contribuíram para o total de vendas.
- **Ticket médio por produto**: Cálculo do valor médio de cada venda por produto.

## 6. 📅 Análise de Recência das Compras

Por fim, exploramos a **recência das compras** dos clientes, ou seja, o tempo desde a última compra de cada cliente. Isso ajuda a identificar clientes que estão mais propensos a realizar uma nova compra e aqueles que podem precisar de um incentivo para voltar.

- **Dias desde a última compra**: Cálculo da quantidade de dias desde a última compra de cada cliente, permitindo segmentar clientes com base na sua recência.

---

A combinação dessas análises oferece uma visão holística do comportamento de compra, das vendas e da performance dos vendedores, permitindo a identificação de oportunidades de melhoria e estratégias para impulsionar os resultados de vendas.


In [0]:
%sql
-- TOP 10 CLIENTES QUE MAIS COMPRARAM EM VALOR

SELECT 
    id_cliente, 
    nome_cliente, 
    SUM(total_compras) AS total_compras
FROM gold.compras_clientes_resumo_mensal
GROUP BY id_cliente, nome_cliente
ORDER BY total_compras DESC LIMIT 10

id_cliente nome_cliente total_compras 58902 StacyVelasquez 102 5462 KennyTanner 101 94800 WayneChan 101 7923 EstherBallard 101 62558 MelodyRhodes 101 30004 RandalCarson 101 69923 AliceSharp 100 37898 AngelGraham 100 41785 HerbertRoth 100 79076 AlexBuck 100

#### 🧐 Observações:

- O cliente **Stacy Velasquez** é o mais ativo do dataset, com **102 compras** registradas.
- A diferença entre o cliente mais ativo e os demais é **muito pequena**, o que sugere um comportamento homogêneo entre os top clientes.
- Seis clientes aparecem com exatamente **101 compras**, reforçando a ideia de um padrão de consumo elevado entre os principais compradores.
- Todos os clientes do top 10 ultrapassam a marca de **100 compras**, o que pode ser um bom critério para **segmentações VIP** ou campanhas de fidelização.

In [0]:
%sql
-- VALOR VENDIDO POR MES E ANO

SELECT ano, mes, SUM(valor_total) AS total_vendas
FROM gold.vendas_resumo_mensal
GROUP BY ano, mes
ORDER BY ano, mes LIMIT 10

ano mes total_vendas 2018 1 1062437807.11 2018 2 957843386.05 2018 3 1064054127.28 2018 4 1028112185.77 2018 5 309095633.51

#### 📈 Observações:

- O **mês de março** foi o melhor período de vendas do ano até o momento, com **mais de R$ 1,06 bilhão** em receita.
- Fevereiro teve o menor volume entre os quatro primeiros meses completos, embora ainda acima de R$ 950 milhões.
- O mês de **maio apresenta uma queda significativa** no volume de vendas, movimentando apenas **R$ 309 milhões**, o que representa uma redução superior a **70%** em relação a abril.

In [0]:
%sql
SELECT descricao_cidade, descricao_pais, vendas_totais
FROM gold.vendas_local
ORDER BY vendas_totais DESC LIMIT 10

descricao_cidade descricao_pais vendas_totais Tucson United States 49838949.39 Jackson United States 49412424.46 Sacramento United States 49183653.65 Fort Wayne United States 48673026.60 Indianapolis United States 48375694.75 Columbus United States 48320438.17 Charlotte United States 48080314.66 San Antonio United States 48062790.91 Phoenix United States 47796465.89 Yonkers United States 47715465.51

#### 📊 Observações:

- As **cidades com as maiores vendas** incluem Tucson, Jackson e Sacramento, com totais variando de **R$ 49,8 milhões a R$ 49,1 milhões**.
- A **diferência** entre as primeiras cidades é relativamente pequena, sugerindo que essas regiões têm desempenhos de vendas bastante próximos.
- A **última cidade da lista**, Yonkers, ainda gera um volume significativo de vendas (**R$ 47,7 milhões**), o que indica uma cobertura sólida em todas essas localidades.

In [0]:
%sql
SELECT nome_vendedor, SUM(total_vendas) AS total
FROM gold.vendas_func
GROUP BY nome_vendedor
ORDER BY total DESC limit 10

nome_vendedor total DevonBrewer 193927551.18 ShelbyRiddle 193353209.02 KatinaMarks 193210942.79 DesireeStuart 193050521.08 DarnellNielsen 192961576.55 WendiBuckley 192764821.41 JulieDyer 192760766.41 ToniaMc Millan 192748076.38 ChadwickCook 192717979.03 HollyCollins 192681441.18

#### 📊 Observações:

- **Devon Brewer** lidera as vendas com um total de **R$ 193,9 milhões**, seguido de perto por **Shelby Riddle** com **R$ 193,4 milhões** e **Katina Marks** com **R$ 193,2 milhões**.
- A diferença entre os **primeiros vendedores** é muito pequena, indicando uma competição acirrada entre os melhores vendedores.
- O desempenho dos **vendedores de topo** é muito homogêneo, com valores bem próximos entre os 10 primeiros colocados, variando de **R$ 193,9 milhões** a **R$ 192,7 milhões**.


In [0]:
%sql
SELECT descricao_produto, vendas_totais
FROM gold.top_produtos
ORDER BY vendas_totais DESC limit 10

descricao_produto vendas_totais Bread - Calabrese Baguette 19276741.70 Shrimp - 31/40 19092223.68 Tia Maria 19082345.75 Puree - Passion Fruit 19077510.94 Zucchini - Yellow 18930851.84 Vanilla Beans 18902234.70 Beef - Inside Round 18738344.12 Grenadine 18711555.22 Lettuce - Treviso 18689692.01 Tuna - Salad Premix 18581137.10

#### 📊 Observações:

- **Bread - Calabrese Baguette** lidera as vendas com um total de **R$ 19,3 milhões**, sendo o produto mais vendido.
- Produtos como **Shrimp - 31/40**, **Tia Maria** e **Puree - Passion Fruit** estão bem próximos em termos de vendas, com **valores próximos a R$ 19 milhões**.
- A **diferenciação entre os produtos** é relativamente pequena, indicando que há uma grande **competição** entre os produtos em termos de vendas.


In [0]:
%sql
SELECT nome_cliente, dias_desde_ultima_compra
FROM gold.recencia_clientes
ORDER BY dias_desde_ultima_compra ASC limit 10 

nome_cliente dias_desde_ultima_compra LloydCochran 23 LamontWilcox 23 CrystalGregory 23 JayWare 23 JermaineSwanson 23 EarlGay 23 AllanBradford 23 LouisBullock 23 SpencerHarrington 23 BethanyHansen 23

#### 📊 Observações

- Todos os clientes têm o mesmo valor de **23 dias desde a última compra**, indicando que a última interação de compra ocorreu no mesmo período para todos esses clientes.
- Isso pode sugerir que os dados foram coletados em um momento específico ou que todos esses clientes realizaram compras em uma janela de tempo muito próxima.


In [0]:
%sql
SELECT descricao_produto, ticket_medio
FROM gold.ticket_medio_produto
ORDER BY ticket_medio DESC limit 10

descricao_produto ticket_medio Shrimp - 31/40 99.87771077026093870974 Beef - Inside Round 99.31756401354739202103 Puree - Passion Fruit 98.82774862980345838643 Bread - Calabrese Baguette 98.59772030955096696316 Zucchini - Yellow 98.45767935342271966048 Tia Maria 98.24764708305230477740 Vanilla Beans 97.83765372670807453416 Tuna - Salad Premix 96.87766996871741397289 Bread - Multigrain 96.51761839870856831380 Lettuce - Treviso 96.40769422421219327250

#### 📊 Observações

- **Produtos com maior ticket médio**: O **Shrimp - 31/40** apresenta o maior ticket médio (99.88), seguido por **Beef - Inside Round** (99.32) e **Puree - Passion Fruit** (98.83).
- **Produtos com menor ticket médio**: O **Lettuce - Treviso** apresenta o menor ticket médio da lista (96.41), embora ainda dentro da faixa de preços relativamente alta.
- A variação entre os valores do ticket médio de todos os produtos não é muito grande, com uma diferença de apenas **3,47** unidades monetárias entre o produto mais caro (Shrimp) e o mais barato (Lettuce).

In [0]:
%sql
SELECT descricao_produto, ultima_compra
FROM gold.ultima_venda_produto
ORDER BY ultima_compra ASC limit 10

descricao_produto ultima_compra Macaroons - Two Bite Choc 2018-05-09 Tahini Paste 2018-05-09 Wine - Crozes Hermitage E. 2018-05-09 Pail With Metal Handle 16l White 2018-05-09 Sprouts - Baby Pea Tendrils 2018-05-09 Bread - Roll, Soft White Round 2018-05-09 Beef - Inside Round 2018-05-09 Cheese - Mozzarella 2018-05-09 Garlic - Primerba, Paste 2018-05-09 Cookies Cereal Nut 2018-05-09

#### 📊 Observações

- **Data Unificada**: Todos os produtos listados foram comprados no mesmo dia, **2018-05-09**, o que pode indicar uma compra em grande quantidade em um único evento ou uma promoção realizada nesse dia.
- **Produtos Variados**: A lista contém uma variedade de produtos, desde alimentos (como **Beef - Inside Round** e **Tahini Paste**) até itens não alimentícios (**Pail With Metal Handle 16l White**), o que pode sugerir que os consumidores compraram de diferentes categorias de produtos no mesmo dia.

# 🤔 Autoavaliação

Acredito que atingi 80% dos objetivos propostos. Consegui construir as 3 camadas da arquitetura, fazer as modelagens necessárias, realizar análises significativas com base nos dados e criar catálogos detalhados. Ponto de melhoria seria investir mais em análises avançadas e visualizações.
